In [1]:
using Pkg
Pkg.activate(".")
using OptimalControl
# using Plots
using ForwardDiff
using DifferentialEquations
using MINPACK
using Statistics
using LinearAlgebra
using PlotlyJS

  Activating project at `c:\Users\uiv02757\OneDrive - Vitesco Technologies\git_repos\preconditioning`
┌ Warning: It looks like the Kaleido process is not responding. 
│ The unresponsive process will be killed, but this means that you will not be able to save figures using `savefig`.
│ 
│ If you are on Windows this might be caused by known problems with Kaleido v0.2 on Windows (you are using version 0.2.1).
│ You might want to try forcing a downgrade of the Kaleido_jll library to 0.1.
│ Check the Package Readme at https://github.com/JuliaPlots/PlotlyKaleido.jl/tree/main#windows-note for more details.
│ 
│ If you think this is not your case, you might try using a longer timeout to check if the process is not responding (defaults to 10 seconds) by passing the desired value in seconds using the `timeout` kwarg when calling `PlotlyKaleido.start` or `PlotlyKaleido.restart`
└ @ PlotlyKaleido C:\Users\uiv02757\.julia\packages\PlotlyKaleido\uMRVG\src\PlotlyKaleido.jl:24


In [2]:
global α = 1

function condition(z, t, integrator)                        # event when condition(z,t,integrator) == 0
    x⁰,x₁,x₂,p⁰,p₁,p₂ = z
    return p₂
end
function affect!(integrator)                                # action when condition == 0 
    global α = -α
    nothing
end

cb = ContinuousCallback(condition, affect!)                 # callback 
H(x, p) = p[1] * x[2] + p[2] * x[3] + α * p[3]
ϕ_ = Flow(Hamiltonian(H), callback = cb)                    # flow with maximizing control 

function ϕ(t0, x0, p0, tf; kwargs...)  
    if p0[3] == 0
        global α = -sign(p0[2])
    else
        global α = sign(p0[3])
    end
    return ϕ_(t0, x0, p0, tf; kwargs...)
end

function ϕ((t0, tf), x0, p0; kwargs...)                     # flow for plot
    if p0[2] == 0
        global α = -sign(p0[2])
    else
        global α = sign(p0[3])
    end
    return ϕ_((t0, tf), x0, p0; kwargs...)
end

t0 = 0; x0 = [0,0,0]; tf = 5; xT = [0,0];                   # initial and final time and state conditions

π((x,p)) = x[2:3];                                          # projection on state space

ϕₓ(p0) = π( ϕ(t0, x0, p0, tf) )                             # state flow
η(p0) = -sqrt.(1 - p0[1].^2 - p0[2]^2)                      # function η(⋅)
ϕₓ₁(p0) = ϕₓ([-1; p0])                                      # normalization 1
ϕₓ₂(p0) = norm(p0) < 1 ? ϕₓ([η(p0); p0]) : [12.5;5]         # normalization 2
# ϕₓ₂(p0) = ϕₓ([η(p0); p0])                                 # normalization 2

# plot 

n = 100
x₁_S₁ = range(-7, 2, n); x₂_S₁ = range(-7, 2, n)
x₁_S₂ = range(-1, 1, n); x₂_S₂ = range(-1, 1, n)
norm_S₁ = zeros(n,n); norm_S₂ = zeros(n,n)
for i ∈ 1:n
    for j ∈ 1:n
        norm_S₁[i,j] = norm(ϕₓ₁([x₁_S₁[i], x₂_S₁[j]]))
        norm_S₂[i,j] = norm(ϕₓ₂([x₁_S₂[i], x₂_S₂[j]]))
    end
end

fig = make_subplots(rows=1, cols=2,  specs=fill(Spec(kind="scene"), 1, 2)) 

layout_1 = Layout( scene = attr(
    xaxis_title="x₁",
    yaxis_title="x₂",
    zaxis_title="||S₁||"))

layout_2 = Layout( scene = attr(
    xaxis_title="x₁",
    yaxis_title="x₂",
    zaxis_title="||S₂||"))

s1 = surface(z = norm_S₁, x = x₁_S₁, y = x₂_S₁)
s2 = surface(z = norm_S₂, x = x₁_S₂, y = x₂_S₂)

p1 = plot(s1, layout_1)
p2 = plot(s2, layout_2)

add_trace!(fig, s1, row=1, col=1)
add_trace!(fig, s2, row=1, col=2)

fig

┌ Warning: Using arrays or dicts to store parameters of different types can hurt performance.
│ Consider using tuples instead.
└ @ SciMLBase C:\Users\uiv02757\.julia\packages\SciMLBase\rR75x\src\performance_warnings.jl:33
┌ Warning: It looks like the Kaleido process is not responding. 
│ The unresponsive process will be killed, but this means that you will not be able to save figures using `savefig`.
│ 
│ If you are on Windows this might be caused by known problems with Kaleido v0.2 on Windows (you are using version 0.2.1).
│ You might want to try forcing a downgrade of the Kaleido_jll library to 0.1.
│ Check the Package Readme at https://github.com/JuliaPlots/PlotlyKaleido.jl/tree/main#windows-note for more details.
│ 
│ If you think this is not your case, you might try using a longer timeout to check if the process is not responding (defaults to 10 seconds) by passing the desired value in seconds using the `timeout` kwarg when calling `PlotlyKaleido.start` or `PlotlyKaleido.restart`


data: [
  "surface with fields scene, type, x, y, and z",
  "surface with fields scene, type, x, y, and z"
]

layout: "layout with fields annotations, margin, scene, scene2, and template"

In [3]:
# global iterate_S2 = Vector{Float64}()                       # global vector to store iterates of the solver

S₁(p0) = ϕₓ₁(p0) - xT
S₂(p0) = ϕₓ₂(p0) - xT                                       # shooting function

# function S₂!(s₂, ξ)                                         # intermediate function
#     push!(iterate_S2, ξ)                                 # stock the iterate
#     return (s₂[:] .= S₂(ξ); nothing)                     
# end
S₂!(s₂, ξ) = (s₂[:] .= S₂(ξ); nothing)
S₁!(s₁, ξ) = (s₁[:] .= S₁(ξ); nothing)


jS₁(ξ) = ForwardDiff.jacobian(S₁, ξ)
jS₂(ξ) = ForwardDiff.jacobian(S₂, ξ)            # compute jacobian by forward differentiation
jS₁!(js₁, ξ) = (js₁ = jS₁(ξ); nothing)                  # intermediate function
jS₂!(js₂, ξ) = (js₂ = jS₂(ξ); nothing)                  # intermediate function

ξ = [-0.77; -0.4]                                            # initial guess
println("Evaluation on ξ : ", S₂(ξ))
println("Jacobian on ξ : ", jS₂(ξ))
# p0_sol = fsolve(S₁!, jS₁!, ξ, show_trace = true)            # solve
p0_sol = fsolve(S₂!, ξ, show_trace = true)            # solve

# println("Iterate : ", iterate_S2)
# println(p0_sol)                                             # print solution
println(p0_sol.x)

sol = ϕ((t0, tf), x0, [η(p0_sol.x); p0_sol.x], 
    saveat=range(t0, tf, 500))                              # get optimal trajectory

# plot
t = sol.t
x⁰ = [sol.u[i][1] for i in 1:length(sol.u)]
x₁ = [sol.u[i][2] for i in 1:length(sol.u)]
x₂ = [sol.u[i][3] for i in 1:length(sol.u)]
p⁰ = [sol.u[i][4] for i in 1:length(sol.u)]
p₁ = [sol.u[i][5] for i in 1:length(sol.u)]
p₂ = [sol.u[i][6] for i in 1:length(sol.u)]
u = sign.(p₂)

p = make_subplots(
    rows=4, cols=2,
    specs=[Spec() Spec(); Spec() Spec(); Spec() Spec(); Spec(colspan=2) missing])

add_trace!(p, scatter(x=t, y=x⁰, name = "x⁰"), row=1, col=1)
add_trace!(p, scatter(x=t, y=p⁰, name = "p⁰"), row=1, col=2)
add_trace!(p, scatter(x=t, y=x₁, name = "x₁"), row=2, col=1)
add_trace!(p, scatter(x=t, y=p₁, name = "p₁"), row=2, col=2)
add_trace!(p, scatter(x=t, y=x₂, name = "x₂"), row=3, col=1)
add_trace!(p, scatter(x=t, y=p₂, name = "p₂"), row=3, col=2)
add_trace!(p, scatter(x=t, y=u,  name = "u" ), row=4, col=1)

relayout!(p)
p

Evaluation on ξ : [-0.23021530000422583, -1.444560441669385]
Jacobian on ξ : [-101.25513566667992 0.06555647001036863; -36.3865289925881 -2.5644012013254742]
Iter     f(x) inf-norm    Step 2-norm      Step time
------   --------------   --------------   --------------
     1     1.444560e+00     0.000000e+00         0.167000
     2     1.250000e+01     2.769126e-01         0.237000
     3     2.304276e+00     7.594941e-02         0.000000
     4     1.250000e+01     7.594941e-02         0.001000
     5     2.304276e+00     7.594941e-02         0.001000
     6     3.786432e+00     1.750212e-02         0.000000
     7     8.791484e-01     5.310098e-03         0.001000
     8     3.917944e+00     1.730704e-02         0.000000
     9     1.557635e+00     5.191298e-03         0.001000
    10     8.462060e-01     1.164460e-03         0.001000
    11     1.282357e+00     4.326760e-03         0.000000
    12     9.409928e-01     1.125527e-03         0.001000
    13     8.688669e-01     1.08169

┌ Warning: It looks like the Kaleido process is not responding. 
│ The unresponsive process will be killed, but this means that you will not be able to save figures using `savefig`.
│ 
│ If you are on Windows this might be caused by known problems with Kaleido v0.2 on Windows (you are using version 0.2.1).
│ You might want to try forcing a downgrade of the Kaleido_jll library to 0.1.
│ Check the Package Readme at https://github.com/JuliaPlots/PlotlyKaleido.jl/tree/main#windows-note for more details.
│ 
│ If you think this is not your case, you might try using a longer timeout to check if the process is not responding (defaults to 10 seconds) by passing the desired value in seconds using the `timeout` kwarg when calling `PlotlyKaleido.start` or `PlotlyKaleido.restart`
└ @ PlotlyKaleido C:\Users\uiv02757\.julia\packages\PlotlyKaleido\uMRVG\src\PlotlyKaleido.jl:24
┌ Warning: It looks like the Kaleido process is not responding. 
│ The unresponsive process will be killed, but this means tha

data: [
  "scatter with fields name, type, x, xaxis, y, and yaxis",
  "scatter with fields name, type, x, xaxis, y, and yaxis",
  "scatter with fields name, type, x, xaxis, y, and yaxis",
  "scatter with fields name, type, x, xaxis, y, and yaxis",
  "scatter with fields name, type, x, xaxis, y, and yaxis",
  "scatter with fields name, type, x, xaxis, y, and yaxis",
  "scatter with fields name, type, x, xaxis, y, and yaxis"
]

layout: "layout with fields annotations, margin, template, xaxis, xaxis2, xaxis3, xaxis4, xaxis5, xaxis6, xaxis7, yaxis, yaxis2, yaxis3, yaxis4, yaxis5, yaxis6, and yaxis7"

In [4]:
n  = 15                                              # number of points for fit : 2n
n_ = 100                                            # number of points for plot: 2n_
p0  = zeros(3, 2*n^2)
p0_ = zeros(3, 2*n_^2)
i = 1;
for a ∈ range(0.0001, 0.9999, n)
    for θ ∈ range(-Base.π, Base.π, n)
        p = [a*cos(θ), a*sin(θ)]
        p0[:,i] = [η(p); p]
        p0[:,n^2+i] = [-η(p); p]
        i = i+1 
    end
end
i = 1
for a ∈ range(0.0001, 0.9999, n_)
    for θ ∈ range(-Base.π, Base.π, n_)
        p = [a*cos(θ), a*sin(θ)]
        p0_[:,i] = [η(p); p] 
        p0_[:,n_^2+i] = [-η(p); p]
        i = i+1
    end
end

x = zeros(3, 2*n^2); p = zeros(3, 2*n^2)                 # init final state and costate
x_ = zeros(3, 2*n_^2); p_ = zeros(3, 2*n_^2)
for i = 1:size(p0,2)
    x[:,i], p[:,i] = ϕ(t0, x0, p0[:,i], tf)           # compute flow for fit
end
for i = 1:size(p0_,2)
    x_[:,i], p_[:,i] = ϕ(t0, x0, p0_[:,i], tf)        # compute flow for plot
end
# a, b, θ, c = fit_ellipse(x[1,:], x[2,:])            # fit ellipse
# r(β) = [[cos(β), sin(β)] [-sin(β), cos(β)]]         # 2x2 rotation matrix
# s(a,b) = [[a,0] [0,b]]                              # 2x2 scale matrix
# β = range(-Base.π, Base.π; length = 100)            # angle for plot ellipse
# xₑ = r(-θ)*s(a,b)*
#     transpose(reduce(hcat,[sin.(β), cos.(β)])).+c   # points of the ellipse

# # construction of the linear diffeomorphism φ(x) = Ax * B
# d = (a*sin(θ))/(b*cos(θ)); β₀ = atan(d)             # intermediate values
# A = r(-β₀)*s(1/a,1/b)*r(θ); B = -A*c                # calculate A and B
# φ(x) = A*x .+ B                                     # function φ

# y = φ(x); y_ = φ(x_); yₑ = φ(xₑ)                    # compute φ on x, x_ and xₑ


trace_1 = scatter(z = x_[1,:], x = x_[2,:], y = x_[3,:], 
    mode = "markers", type = "scatter3d",
    title = "a",
    marker=attr(
        size=2,
        color=sign.(p_[1,:]),                # set color to an array/list of desired values
        colorscale="Viridis",   # choose a colorscale
        opacity=0.8
    )        
)

layout_1 = Layout( 
            width=600, height=400,
            scene = attr(
                    xaxis_title="x₁",
                    yaxis_title="x₂",
                    zaxis_title="x⁰"
            ),	
        )

Plot([trace_1], layout_1)
   
# add_trace!(fig,
#     surface(z = norm_S₂, x = x₁_S₂, y = x₂_S₂),
#     row = 1, col = 2)

┌ Warning: It looks like the Kaleido process is not responding. 
│ The unresponsive process will be killed, but this means that you will not be able to save figures using `savefig`.
│ 
│ If you are on Windows this might be caused by known problems with Kaleido v0.2 on Windows (you are using version 0.2.1).
│ You might want to try forcing a downgrade of the Kaleido_jll library to 0.1.
│ Check the Package Readme at https://github.com/JuliaPlots/PlotlyKaleido.jl/tree/main#windows-note for more details.
│ 
│ If you think this is not your case, you might try using a longer timeout to check if the process is not responding (defaults to 10 seconds) by passing the desired value in seconds using the `timeout` kwarg when calling `PlotlyKaleido.start` or `PlotlyKaleido.restart`
└ @ PlotlyKaleido C:\Users\uiv02757\.julia\packages\PlotlyKaleido\uMRVG\src\PlotlyKaleido.jl:24
┌ Warning: It looks like the Kaleido process is not responding. 
│ The unresponsive process will be killed, but this means tha

data: [
  "scatter3d with fields marker, mode, title, type, x, y, and z"
]

layout: "layout with fields height, margin, scene, template, and width"

In [32]:
# Traduction of the matlab code : https://fr.mathworks.com/matlabcentral/fileexchange/24693-ellipsoid-fit
function fit_ellipse(x, y, z)
    # quadratic form of ellipse
    D = hcat( 
        x .* x + y .* y - 2 .* z .* z,
        x .* x + z .* z - 2 .* y .* y,
        2 .* x .* y,
        2 .* x .* z,
        2 .* y .* z,
        2 .* x,
        2 .* y,
        2 .* z,
        1 .* ones(size(x)))            
    
    d2 = x .* x + y .* y + z .* z;      # the RHS of the llsq problem (y's)
    u = (D' * D)\(D' * d2);             # solution to the normal equations
    # find the residual sum of errors
    # chi2 = sum( ( 1 - ( D * u ) ./ d2 ).^2 ); % this chi2 is in the coordinate frame in which the ellipsoid is a unit sphere.

    # find the ellipsoid parameters
    # convert back to the conventional algebraic form
    v = zeros(10,)
    v[1] = u[1] + u[2] - 1;
    v[2] = u[1] - 2 * u[2] - 1;
    v[3] = u[2] - 2 * u[1] - 1;
    v[4:10] = u[3:9];
    
    # form the algebraic form of the ellipsoid
    A = [   v[1] v[4] v[5] v[7];
            v[4] v[2] v[6] v[8];
            v[5] v[6] v[3] v[9];
            v[7] v[8] v[9] v[10] 
        ];

    # find the center of the ellipsoid
    center = -A[1:3,1:3] \ v[7:9];
    T = Matrix{Base.Float64}(I, 4, 4)
    T[4,1:3] = center[1:3];
    
    # translate to the center
    R = T * A * transpose(T);

    # solve the eigenproblem
    evals = eigvals(R[1:3,1:3] / -R[4,4])
    evecs = eigvecs(R[1:3,1:3] / -R[4,4])

    radii = sqrt.( 1 ./ abs.(evals) )
    sgns = sign.(evals)
    radii = radii .* sgns

    return [center, radii, evecs]
end

function plot_ellipsoid(center, coefs, ngrid=25)
    # Radii corresponding to the coefficients:
    rx, ry, rz = 1 ./ sqrt.(coefs)

    # Set of all spherical angles:
    u = range(0, 2pi, length=ngrid)
    v = range(0, pi, length=ngrid)

    # Cartesian coordinates that correspond to the spherical angles:
    # (this is the equation of an ellipsoid):
    x = [coefs[1] * x * y for (x, y) in Iterators.product(cos.(u), sin.(v))]
    y = [coefs[2] * x * y for (x, y) in Iterators.product(sin.(u), sin.(v))]
    z = [coefs[3] * x * y for (x, y) in Iterators.product(ones(length(u)), cos.(v))]
    return x .+ center[1], y .+ center[2], z .+ center[3]
end
# Plot:

center, radii, evecs = fit_ellipse(x_[1,:], x_[2,:], x_[3,:])


3-element Vector{Array{Float64}}:
 [0.004359724028509095, 0.001625063420949556, 0.000359336701272004]
 [47.54396566195552, 4.11283735251359, 0.8369654605644872]
 [0.8938501925805334 0.3985461743169627 0.20540881227702062; 0.4342068836843456 -0.6552205248064996 -0.6181831816164401; 0.11178647228029115 -0.6417530761980097 0.7587204846354944]

In [33]:
println(norm(evecs[1,:]), norm(evecs[1,:]), norm(evecs[1,:]))
print(transpose(evecs[1,:])*evecs[2,:], transpose(evecs[1,:])*evecs[3,:], transpose(evecs[2,:])*evecs[3,:] )

0.99999999999999990.99999999999999990.9999999999999999
-1.1102230246251565e-165.551115123125783e-17-1.1102230246251565e-16

In [37]:
trace_1 = scatter(z = x_[1,:], x = x_[2,:], y = x_[3,:], 
    mode = "markers", type = "scatter3d",
    name = "Datas",
    marker=attr(
        size=2,
        color=sign.(p_[1,:]),                # set color to an array/list of desired values
        colorscale="Viridis",   # choose a colorscale
        opacity=0.8
    )        
)
trace_C = scatter(z = [center[1]], x = [center[2]], y = [center[3]], 
    mode = "markers", type = "scatter3d", name = "Center", marker=attr(size=5))

trace_P1 = scatter( z = [center[1], center[1] + radii[1]/2 * evecs[1,1]], 
                    x = [center[2], center[2] + radii[1]/2 * evecs[1,2]], 
                    y = [center[3], center[3] + radii[1]/2 * evecs[1,3]], 
    mode = "lines+markers", type = "scatter3d", name = "P1", marker=attr(size=3))
trace_P2 = scatter( z = [center[1], center[1] + radii[2]/2 * evecs[2,1]], 
                    x = [center[2], center[2] + radii[2]/2 * evecs[2,2]], 
                    y = [center[3], center[3] + radii[2]/2 * evecs[2,3]], 
    mode = "lines+markers", type = "scatter3d", name = "P2", marker=attr(size=3))
trace_P3 = scatter( z = [center[1], center[1] + radii[3]/2 * evecs[3,1]], 
                    x = [center[2], center[2] + radii[3]/2 * evecs[3,2]], 
                    y = [center[3], center[3] + radii[3]/2 * evecs[3,3]], 
    mode = "lines+markers", type = "scatter3d", name = "P3", marker=attr(size=3))

layout_1 = Layout( 
            width=600, height=400,
            scene = attr(
                    xaxis_title="x₁",
                    yaxis_title="x₂",
                    zaxis_title="x⁰"
            ),	
        )

Plot([trace_1, trace_C, trace_P1, trace_P2, trace_P3], layout_1)

┌ Warning: It looks like the Kaleido process is not responding. 
│ The unresponsive process will be killed, but this means that you will not be able to save figures using `savefig`.
│ 
│ If you are on Windows this might be caused by known problems with Kaleido v0.2 on Windows (you are using version 0.2.1).
│ You might want to try forcing a downgrade of the Kaleido_jll library to 0.1.
│ Check the Package Readme at https://github.com/JuliaPlots/PlotlyKaleido.jl/tree/main#windows-note for more details.
│ 
│ If you think this is not your case, you might try using a longer timeout to check if the process is not responding (defaults to 10 seconds) by passing the desired value in seconds using the `timeout` kwarg when calling `PlotlyKaleido.start` or `PlotlyKaleido.restart`
└ @ PlotlyKaleido C:\Users\uiv02757\.julia\packages\PlotlyKaleido\uMRVG\src\PlotlyKaleido.jl:24
┌ Warning: It looks like the Kaleido process is not responding. 
│ The unresponsive process will be killed, but this means tha

data: [
  "scatter3d with fields marker, mode, name, type, x, y, and z",
  "scatter3d with fields marker, mode, name, type, x, y, and z",
  "scatter3d with fields marker, mode, name, type, x, y, and z",
  "scatter3d with fields marker, mode, name, type, x, y, and z",
  "scatter3d with fields marker, mode, name, type, x, y, and z"
]

layout: "layout with fields height, margin, scene, template, and width"